# TensorFlow vs Keras

I have been very curious about comparing these two packages.  Last summer on a project, our intern selected Keras over everything else because she said it was much easier to use.  She is not the only one who thinks that...

Keras is the [first](http://www.fast.ai/2017/01/03/keras/) *higher-level interface* to be directly integrated into TensorFlow.  I love this comment: **Using TensorFlow makes me feel like I’m not smart enough to use TensorFlow; whereas using Keras makes me feel like neural networks are easier than I realized.**

Let's get started by building a CNN (Convolutional Neural Network) using both TensorFlow and Keras for recognizing handwriting images from the MNIST library of symbols - the classic example.

Per my usual curiosity, I start asking questions like "what is a CNN?"  This is an involved topic, so I am going to give some references to go through and leave it to the reader to give due diligence.

Christopher Olah.  Understanding Convolutions.  http://colah.github.io/posts/2014-07-Understanding-Convolutions/  
Christopher Olah.  Conv Nets: A Modular Perspective.  http://colah.github.io/posts/2014-07-Conv-Nets-Modular/  
DeepLearning.ai. Convolutional Neural Nets (LeNet). http://deeplearning.net/tutorial/lenet.html  
[CS231n: Convolutional Neural Networks for Visual Recognition](http://cs231n.stanford.edu/) Notes, see especially Module 2.  http://cs231n.github.io/  
*Deep Learning Book*, Chapter 9, Convolutional Networks.  http://www.deeplearningbook.org/contents/convnets.html  


# TensorFlow

For TensorFlow, I follow the [tutorial](https://www.tensorflow.org/tutorials/layers) on layers provided by TensorFlow.

### CNN architecture

* [Convolutional Layer](https://www.tensorflow.org/api_docs/python/tf/nn/conv2d) \#1: Applies 32 5x5 filters (extracting 5x5-pixel subregions), with ReLU activation function
* [Pooling Layer](https://www.tensorflow.org/versions/r1.2/api_docs/python/tf/layers/max_pooling2d) \#1: Performs max pooling with a 2x2 filter and stride of 2 (which specifies that pooled regions do not overlap)
* [Convolutional Layer](https://www.tensorflow.org/api_docs/python/tf/nn/conv2d) \#2: Applies 64 5x5 filters, with ReLU activation function
* [Pooling Layer](https://www.tensorflow.org/versions/r1.2/api_docs/python/tf/layers/max_pooling2d) \#2: Again, performs max pooling with a 2x2 filter and stride of 2
* [Dense Layer](https://www.tensorflow.org/versions/master/api_docs/python/tf/layers/dense) \#1: 1,024 neurons, with dropout regularization rate of 0.4 (probability of 0.4 that any given element will be dropped during training)
* [Dense Layer](https://www.tensorflow.org/versions/master/api_docs/python/tf/layers/dense) \#2 (Logits Layer): 10 neurons, one for each digit target class (0–9).

and a [dropout](https://www.tensorflow.org/api_docs/python/tf/layers/dropout) layer.

In [1]:
# Imports
import numpy as np
import tensorflow as tf
import time

tf.logging.set_verbosity(tf.logging.INFO)

def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    # -1 - batch size for a 28x28 image with 1 color channel
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1.
    # 32 5x5 filters
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # Pooling Layer #1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2 and Pooling Layer #2
    # 64 5x5 filters
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)
    
    # Pooling layer #2
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Dense Layer
    # 1,024 neurons, with dropout regularization rate of 0.4
    # probability of 0.4 that any given element will be dropped during training)
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(
        inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits Layer
    # 10 neurons, one for each digit target class (0–9)
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
        # Generate predictions (for PREDICT and EVAL mode)
        "classes": tf.argmax(input=logits, axis=1),
        # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
        # `logging_hook`.
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

### Import Dataset

Import the mnist database.

In [2]:
mnist = tf.contrib.learn.datasets.load_dataset("mnist")

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


### Training Data

In [3]:
train_data = mnist.train.images # Returns np.array
print(train_data.shape)

(55000, 784)


In [4]:
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
print(type(train_labels))
print(train_labels.shape)

<class 'numpy.ndarray'>
(55000,)


### Testing Data

In [5]:
test_data = mnist.test.images # Returns np.array
test_labels = np.asarray(mnist.test.labels, dtype=np.int32)
print(test_data.shape)

(10000, 784)


On Dimensions:
* 784 is the number of bytes in a 28x28x1 image
* Of the images, nearly 85% are for training and the remaining are for testing.

### Create the Estimator
The Estimator is a TensorFlow class for performing high-level model training, evaluation, and inference for the model.

In [6]:
# Create the Estimator
mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir="tmp/mnist_convnet_model")

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {}


### Set Up a Logging Hook

Since CNNs can take a while to train, let's set up some logging so we can track progress during training. We can use TensorFlow's tf.train.SessionRunHook to create a tf.train.LoggingTensorHook that will log the probability values from the softmax layer of our CNN.

In [7]:
# Set up logging for predictions
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
    tensors=tensors_to_log, every_n_iter=50)

## Train the Model
On this free-tier notebook server, this is terribly slow taking up to one hour of CPU according to the documentation.  It is better to run this on compute with GPU. <a href="#after_compute">Go to after compute.</a>

In [8]:
# Train the model
start=time.time()

train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

print("Training (TensorFlow) Elaspsed Time: {}".format(time.time()-start))


INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Restoring parameters from tmp/mnist_convnet_model/model.ckpt-118850
INFO:tensorflow:Saving checkpoints for 118851 into tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:loss = 0.0264696, step = 118851
INFO:tensorflow:probabilities = [[ 0.00000164  0.99994838  0.00003752  0.00000001  0.0000004   0.
   0.00000002  0.00000471  0.00000724  0.00000005]
 [ 0.99992502  0.00000001  0.00007234  0.          0.          0.
   0.00000007  0.00000012  0.00000219  0.00000026]
 [ 0.00000377  0.00000013  0.00001008  0.00006576  0.          0.00000002
   0.          0.99990416  0.00000022  0.00001587]
 [ 0.00012844  0.00006522  0.00016634  0.02313622  0.00004533  0.01551746
   0.00024823  0.00001443  0.95957649  0.00110184]
 [ 0.          0.          0.          0.00380084  0.00000001  0.99607408
   0.00000004  0.00000002  0.00004618  0.00007884]
 [ 0.00036087  0.00002192  0.00025407  0.00233775  0.00000475  0.00121548
   0.00208266  0.00000

INFO:tensorflow:probabilities = [[ 0.0000001   0.00000288  0.99826884  0.00112817  0.          0.          0.
   0.          0.00059999  0.        ]
 [ 0.          0.          0.          0.          0.9999994   0.          0.
   0.00000054  0.          0.00000001]
 [ 0.          0.00000001  0.00000215  0.00000012  0.          0.          0.
   0.9999975   0.          0.00000027]
 [ 0.00000035  0.99972028  0.00000616  0.00001471  0.00013053  0.0000017
   0.00000537  0.00000726  0.00010543  0.00000823]
 [ 0.00000005  0.00000003  0.99999928  0.00000013  0.          0.          0.
   0.00000002  0.00000046  0.        ]
 [ 0.00006729  0.00000196  0.00005385  0.00064888  0.00009744  0.00015921
   0.00769839  0.00001227  0.9910357   0.00022494]
 [ 0.          0.          0.00000004  0.99999952  0.          0.00000019
   0.          0.00000001  0.0000002   0.00000002]
 [ 0.00000003  0.          0.          0.          0.00000002  0.00000029
   0.99999976  0.          0.00000003  0.        ]
 

INFO:tensorflow:global_step/sec: 2.0478
INFO:tensorflow:loss = 0.0162056, step = 118951 (48.834 sec)
INFO:tensorflow:probabilities = [[ 0.00000139  0.00000438  0.00002462  0.00000506  0.00000773  0.00001003
   0.          0.98461837  0.00000112  0.01532715]
 [ 0.          0.          0.00000001  0.99999988  0.          0.          0.
   0.          0.00000004  0.00000013]
 [ 0.          0.          0.00000001  0.99999738  0.          0.00000001
   0.          0.00000004  0.00000225  0.00000037]
 [ 0.          0.          0.          1.          0.          0.00000003
   0.          0.          0.          0.        ]
 [ 0.          0.00000149  0.00000006  0.          0.99998975  0.00000001
   0.          0.00000868  0.          0.00000003]
 [ 0.00000036  0.00140902  0.00000478  0.00000473  0.00011654  0.0011901
   0.99685585  0.          0.00041837  0.00000014]
 [ 0.00001628  0.00011818  0.00001576  0.00002345  0.00220265  0.00000286
   0.          0.99676311  0.00000591  0.00085177]
 

INFO:tensorflow:probabilities = [[ 0.00000129  0.00002518  0.00000057  0.00002579  0.00420489  0.00016921
   0.00000005  0.00024185  0.00000155  0.99532962]
 [ 0.          0.          0.          0.99999976  0.          0.00000007
   0.          0.          0.00000007  0.        ]
 [ 0.00000008  0.00000285  0.000005    0.          0.99995828  0.00000003
   0.0000319   0.          0.00000153  0.00000027]
 [ 0.00000014  0.99933088  0.00000484  0.00001375  0.00019167  0.00000129
   0.00000068  0.00009935  0.00025899  0.00009838]
 [ 0.00000001  0.00000001  0.00043508  0.00188019  0.          0.          0.
   0.99762291  0.00000035  0.00006144]
 [ 0.00028603  0.00499877  0.9433254   0.0081262   0.00000003  0.00000001
   0.          0.01619039  0.02675923  0.00031384]
 [ 0.00001446  0.00001555  0.00078131  0.00017397  0.00000009  0.00000072
   0.00000057  0.00000014  0.99900752  0.00000573]
 [ 0.00000047  0.00000204  0.00000119  0.00001561  0.0001492   0.02963961
   0.97017306  0.          

INFO:tensorflow:global_step/sec: 1.39637
INFO:tensorflow:loss = 0.0111866, step = 119051 (71.835 sec)
INFO:tensorflow:probabilities = [[ 0.99971896  0.00000534  0.0001753   0.00000135  0.          0.00002704
   0.00000725  0.00004471  0.00001845  0.00000157]
 [ 0.0002015   0.00001305  0.00001123  0.00000599  0.00112972  0.00013986
   0.99840921  0.00000105  0.00008398  0.0000045 ]
 [ 0.00000408  0.00001468  0.00000109  0.00000016  0.00044835  0.00000691
   0.9995203   0.00000001  0.00000368  0.00000067]
 [ 0.06513887  0.          0.00000004  0.00000023  0.00000089  0.00000779
   0.93478     0.00000146  0.00006265  0.00000814]
 [ 0.00000006  0.00000225  0.00000346  0.00000076  0.00000495  0.00009556
   0.99989223  0.          0.00000077  0.        ]
 [ 0.          0.          0.          0.00000024  0.          0.99911612
   0.          0.          0.00000037  0.00088321]
 [ 0.99997866  0.00000001  0.00000041  0.00000024  0.          0.00000453
   0.00000025  0.00000388  0.00000341  0.0

...

INFO:tensorflow:global_step/sec: 2.02588
INFO:tensorflow:loss = 0.0128799, step = 138651 (49.360 sec)
INFO:tensorflow:probabilities = [[ 0.00000181  0.0000001   0.00002487  0.00000825  0.00029731  0.00000266
   0.00000014  0.01663991  0.00006568  0.98295927]
 [ 0.99096137  0.00000023  0.00011069  0.00000498  0.00000001  0.00004237
   0.00000462  0.00000033  0.00887405  0.00000131]
 [ 0.99751031  0.0000001   0.00005476  0.00000033  0.00002425  0.00006695
   0.00036931  0.00024176  0.0000269   0.00170533]
 [ 0.          0.          0.          0.00000003  0.          0.99999893
   0.00000111  0.          0.          0.        ]
 [ 0.          0.00000058  0.00034379  0.99964976  0.          0.00000577
   0.          0.          0.0000001   0.        ]
 [ 0.00000019  0.00000005  0.00000071  0.00023353  0.00000182  0.9990865
   0.00004652  0.00000001  0.00059654  0.00003427]
 [ 1.          0.          0.          0.          0.          0.
   0.00000002  0.          0.          0.        ]


INFO:tensorflow:probabilities = [[ 0.00000798  0.00000005  0.00000019  0.0000003   0.00000152  0.00002412
   0.99995875  0.          0.00000697  0.00000008]
 [ 0.00000649  0.00000008  0.00000072  0.          0.00404828  0.00000015
   0.9959442   0.          0.          0.00000009]
 [ 0.98876047  0.          0.00000029  0.00000723  0.00000011  0.00010326
   0.00013506  0.01019235  0.00002159  0.00077974]
 [ 0.00001348  0.00001128  0.00000463  0.000009    0.00000492  0.0000015
   0.00000008  0.99988258  0.000001    0.00007156]
 [ 0.          0.          0.          0.00001098  0.          0.99998868
   0.00000012  0.          0.00000002  0.00000026]
 [ 0.00000049  0.          0.00000068  0.00000032  0.00000005  0.00000005
   0.          0.99999332  0.00000033  0.00000483]
 [ 0.          0.          0.00000009  0.00004473  0.00000003  0.0000056
   0.          0.00000009  0.9999491   0.00000033]
 [ 0.00000066  0.99937457  0.0000001   0.00000013  0.00007528  0.00000175
   0.00001248  0.0003

INFO:tensorflow:global_step/sec: 2.10668
INFO:tensorflow:loss = 0.0286419, step = 138751 (47.468 sec)
INFO:tensorflow:probabilities = [[ 0.00000001  0.          0.00000116  0.00000199  0.0000035   0.          0.
   0.00001976  0.00000008  0.99997342]
 [ 0.00000051  0.          0.          0.          0.          0.00000055
   0.99999046  0.          0.00000846  0.        ]
 [ 0.00027106  0.00000532  0.00004471  0.00000037  0.00641027  0.00005512
   0.99320155  0.00000497  0.00000357  0.00000296]
 [ 0.00000001  0.          0.          0.00001112  0.00000076  0.00000075
   0.          0.00000153  0.00001528  0.99997056]
 [ 0.9999541   0.00000021  0.00000052  0.          0.00000002  0.0000019
   0.00000696  0.00003458  0.00000162  0.00000004]
 [ 0.00000009  0.00002534  0.00000252  0.00000421  0.00000707  0.00000003
   0.00000032  0.00000016  0.99995923  0.00000102]
 [ 0.00000004  0.9999311   0.00000005  0.00000001  0.0000038   0.
   0.00000001  0.00006238  0.00000254  0.00000006]
 [ 0.   

INFO:tensorflow:probabilities = [[ 0.00000052  0.9995091   0.00000211  0.00000053  0.0000855   0.00000001
   0.00000066  0.00038864  0.00001285  0.00000016]
 [ 0.          0.00000021  0.00000149  0.00235183  0.00001515  0.00000014
   0.          0.00000468  0.00001804  0.99760842]
 [ 0.00000003  0.00000171  0.00001234  0.00004765  0.00000001  0.001635
   0.00000037  0.00000013  0.99828869  0.00001406]
 [ 0.00000008  0.99993503  0.00000037  0.00000153  0.00000615  0.00000002
   0.0000005   0.00002367  0.00003243  0.00000036]
 [ 0.00000002  0.00000572  0.00000001  0.10380463  0.00000042  0.89616156
   0.00000084  0.          0.00002657  0.0000002 ]
 [ 0.00000121  0.00000049  0.00012074  0.00023931  0.00000001  0.00000105
   0.          0.00001214  0.99961865  0.00000645]
 [ 0.00116326  0.00017651  0.00029227  0.00000546  0.00001302  0.00002455
   0.00001615  0.00002943  0.99817848  0.00010086]
 [ 0.          0.          0.00000001  0.00000058  0.00065176  0.00003677
   0.          0.0000

INFO:tensorflow:Saving checkpoints for 138813 into tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Saving checkpoints for 138850 into tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.0361591.
Training (TensorFlow) Elaspsed Time: 10844.700640916824


<p id="after_compute">Note it took 10845 seconds or over 3 hours to train without GPU.  That is why these problems have to be run with GPU.</p>

## Evaluate the Model

In [17]:
# Evaluate the model and print results
start=time.time()

eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": test_data},
    y=test_labels,
    num_epochs=1,
    shuffle=False)
test_results = mnist_classifier.evaluate(input_fn=eval_input_fn)

print("Testing (TensorFlow) Elaspsed Time: {}".format(time.time()-start))

print(test_results)

INFO:tensorflow:Finished evaluation at 2018-03-29-12:16:26
INFO:tensorflow:Saving dict for global step 138850: accuracy = 0.989, global_step = 138850, loss = 0.0328141
Testing (TensorFlow) Elaspsed Time: 22.45904016494751
{'accuracy': 0.98900002, 'loss': 0.032814112, 'global_step': 138850}


# Keras

Consider building a [CNN with Keras](https://elitedatascience.com/keras-tutorial-deep-learning-in-python). The network is modified to match the TensorFlow network given above and updated to the current version of Keras as of March 2018.

In [23]:
# 1. Import libraries and modules
import time

import numpy as np
np.random.seed(123)  # for reproducibility
 
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten
from keras.layers import Convolution2D, MaxPooling2D
from keras.utils import np_utils
from keras.datasets import mnist
 
# 2. Load pre-shuffled MNIST data into train and test sets
(X_train, y_train), (X_test, y_test) = mnist.load_data()
 
# 3. Preprocess input data
X_train = X_train.reshape(X_train.shape[0], 28, 28, 1)
X_test = X_test.reshape(X_test.shape[0], 28, 28, 1)
X_train = X_train.astype('float32')
X_test = X_test.astype('float32')
X_train /= 255
X_test /= 255
 
# 4. Preprocess class labels
Y_train = np_utils.to_categorical(y_train, 10)
Y_test = np_utils.to_categorical(y_test, 10)

Notice how Keras states it is using the TensorFlow backend.

### CNN architecture

* [Convolutional Layer](https://faroit.github.io/keras-docs/1.2.2/layers/convolutional/#convolution2d) \#1: Applies 32 5x5 filters (extracting 5x5-pixel subregions), with ReLU activation function
* [Pooling Layer](https://keras.io/layers/pooling/#maxpooling2d) \#1: Performs max pooling with a 2x2 filter and stride of 2 (which specifies that pooled regions do not overlap)
* [Convolutional Layer](https://faroit.github.io/keras-docs/1.2.2/layers/convolutional/#convolution2d) \#2: Applies 64 5x5 filters, with ReLU activation function
* [Pooling Layer](https://keras.io/layers/pooling/#maxpooling2d) \#2: Again, performs max pooling with a 2x2 filter and stride of 2
* [Dense Layer](https://keras.io/layers/core/#dense) \#1: 1,024 neurons, with dropout regularization rate of 0.4 (probability of 0.4 that any given element will be dropped during training)
* [Dense Layer](https://keras.io/layers/core/#dense) \#2 (Logits Layer): 10 neurons, one for each digit target class (0–9).

and the [Dropout](https://keras.io/layers/core/#dropout) layer.

In [24]:
# 5. Define model architecture
model = Sequential()

model.add(Convolution2D(32, (5, 5), activation='relu', input_shape=(28,28,1)))
model.add(MaxPooling2D(pool_size=(2,2), strides=2))
model.add(Convolution2D(64, (5, 5), activation='relu'))
model.add(MaxPooling2D(pool_size=(2,2), strides=2))
model.add(Flatten())
model.add(Dense(1024, activation='relu'))
model.add(Dropout(0.4))
model.add(Dense(10, activation='softmax'))

In [25]:
# 6. Compile model
model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
 

In [26]:
# 7. Fit model on training data
start=time.time()

model.fit(X_train, Y_train, 
          batch_size=32, epochs=10, verbose=1)

print("Training (Keras) Elaspsed Time: {}".format(time.time()-start))

Epoch 1/10
60000/60000 [==============================] - 184s 3ms/step - loss: 0.1174 - acc: 0.9634
Epoch 2/10
60000/60000 [==============================] - 175s 3ms/step - loss: 0.0425 - acc: 0.9873
Epoch 3/10
60000/60000 [==============================] - 175s 3ms/step - loss: 0.0304 - acc: 0.9907
Epoch 4/10
60000/60000 [==============================] - 238s 4ms/step - loss: 0.0241 - acc: 0.9925 1s - loss: 0.0242 - a
Epoch 5/10
60000/60000 [==============================] - 216s 4ms/step - loss: 0.0202 - acc: 0.9937
Epoch 6/10
60000/60000 [==============================] - 170s 3ms/step - loss: 0.0169 - acc: 0.9947
Epoch 7/10
60000/60000 [==============================] - 157s 3ms/step - loss: 0.0150 - acc: 0.9953
Epoch 8/10
60000/60000 [==============================] - 148s 2ms/step - loss: 0.0110 - acc: 0.9968
Epoch 9/10
60000/60000 [==============================] - 144s 2ms/step - loss: 0.0134 - acc: 0.9962
Epoch 10/10
60000/60000 [==============================] - 146s 2ms/s

In [27]:
# 8. Evaluate model on test data
start=time.time()

score = model.evaluate(X_test, Y_test, verbose=0)

print("Testing (Keras) Elaspsed Time: {}".format(time.time()-start))

print("Loss={}, Accuracy={}".format(score[0], score[1]))

Testing (Keras) Elaspsed Time: 8.290692329406738
Loss=0.05543863881601328, Accuracy=0.9902


### Visualizing Keras Models

We found this later, but following is how to visualize the network.  This is the CNN we are using.

In [28]:
from keras.utils.vis_utils import plot_model
plot_model(model, to_file="images/keras_cnn.png", show_shapes=True, show_layer_names=True)

import time
time.sleep(1)

<img src="images/keras_cnn.png">

# Summary

Admittedly, Keras does present a better (less complicated) interface then TensorFlow, but I really struggled a bit around building up the layers.  It seemed to me that the shorthand was a bit too terse and I had to work a bit to get through a few issues with the Convolution2D layer.

There are a couple of other things to really like about Keras.  Whereas in TensorFlow we had to jump through hoops to see what was going on, Keras presented a simple way to print out progress.

The next thing I noticed is that Keras is amazingly fast - but how can that be since TensorFlow is the backend?  It might be a question of how the two packages handle the computing environment (multi-threading, GPU usage).
We can run a few studies and tests to determine if this is the case.  First, the TensorFlow documentation for the [convolution](https://www.tensorflow.org/api_docs/python/tf/nn/conv2d) has a flag for running CUDA on GPUs.  The question is, what does this notebook have in the way of CPUs and GPUs?

In [29]:
import multiprocessing
import tensorflow as tf

print('Number of CPU Cores: {}'.format(multiprocessing.cpu_count()))

print('GPU available for TensorFlow : {}'.format(tf.test.is_gpu_available()))

Number of CPU Cores: 2
GPU available for TensorFlow : False


Since Keras runs the training in under one hour with three times the steps as TensorFlow, I am befuddled as to why the performance is so much better.  I note that with the extra training, Keras is delivering better accuracy with less loss, but there could be another factor - perhaps I did not get the network correct?  I just don't know, but as I continue on in my journey, it might be good to revisit this...

**What about Theano?**  The [DeepLearning.ai reference](http://deeplearning.net/tutorial/lenet.html) uses [Theano](http://deeplearning.net/software/theano/).  Theano is another low-level compute engine like TensorFlow.  There are [many opinions](https://www.reddit.com/r/MachineLearning/comments/4ekywt/tensorflow_vs_theano_which_to_learn/) on which to learn.  That is why Keras is so powerful - Keras also [wraps](https://keras.io/backend/) on top of Theano!

In coming presentations, I will be looking at more models using Keras.  But I suspect that there will be constructs in TensorFlow and Theano not available in Keras.  To me, it appears that learning Keras first is likely best - that is how some courses on Udemy approach it.  However, knowing the backends like TensorFlow or Theano well enough to implement those special cases not handled by Keras will likely be necessary.